In [7]:
#Steps for today:
#Import the data (V&J)
#Exploring the features (V&J)
#Clean and normalize the data (V&J)
#Decide on a classification algorithm (V&J)
#First trainings (V&J)
#Calculate the scoring and tweak/consolidate features accordingly (V&J)
#First submission
#!pip3 install markupsafe==2.0.1
#!conda install -y -c conda-forge pandas-profiling
#!pip install pandas-profiling
#!pip install category-encoders
!pip install ipywidgets

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.4/123.4 kB 1.7 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 245.3/245.3 kB 4.2 MB/s eta 0:00:00a 0:00:01
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 9.1 MB/s eta 0:00:00a 0:00:01m


In [8]:
from pandas_profiling import ProfileReport
import warnings
warnings.filterwarnings('ignore')
import pandas as pd
import numpy as np
import category_encoders as ce
from pathlib import Path
import matplotlib.pyplot as plt

In [9]:
train_values = pd.read_csv('train_values.csv', sep=',')
train_labels = pd.read_csv('train_labels.csv', sep=',')
x_test = pd.read_csv('test_values.csv', sep=',')

#We only use the first 10000 data points
prof = ProfileReport(train_values)
prof

Render HTML: 100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:02<00:00,  2.19s/it]


In [10]:
#Encode

 ce_te = ce.TargetEncoder(cols=["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"])
    
def encode_values(normalized_train_values,X,y):
   
    #columns to perform encoding for train data

    #create an object of the Targetencoder
    ce_te.fit(X,y)
    encoded_columns = ce_te.transform(X)
    #normalized_train_values = train_values.copy()
    # selecting old value
    normalized_train_values[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]] = encoded_columns[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]]
    new_normalized_train_values= normalized_train_values.drop(columns=['building_id'])

    adapted_train_labels = train_labels.drop(columns=['building_id']).values.flatten()

    
    
X = train_values[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]]
y = train_values['building_id']    
encode_values(train_values.copy()X,y)






In [11]:
#columns to perform encoding for test data
X_test = x_test[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]]
y_test = x_test['building_id']

#create an object of the Targetencoder
ce_te.fit(X_test,y_test)
encoded_columns_test = ce_te.transform(X_test)
#normalized_train_values_test = x_test.copy()

# selecting old value
normalized_train_values_test[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]] = encoded_columns_test[["land_surface_condition","foundation_type","roof_type","ground_floor_type","other_floor_type","position","plan_configuration","legal_ownership_status"]]
new_normalized_train_values_test= normalized_train_values_test.drop(columns=['building_id'])
new_normalized_train_values_test

encode_values(x_test.copy())


NameError: name 'ce_te' is not defined

In [5]:
#Import Random Forest Model
#from sklearn.ensemble import RandomForestClassifier
from sklearn import tree

#Train the model using the training sets y_pred=clf.predict(X_test)
clf = tree.DecisionTreeClassifier()
clf = clf.fit(new_normalized_train_values,adapted_train_labels)
y_pred=clf.predict(new_normalized_train_values_test)

In [6]:
from sklearn.model_selection import cross_val_score

#10-Fold Cross validation
print(np.mean(cross_val_score(clf, new_normalized_train_values, adapted_train_labels)))

0.6572115926069251


In [100]:
#Get submission ready for random forest attempt
import base64

submission_random_forest = x_test["building_id"]
i = pd.DataFrame(np.array(y_pred))

submission_concatenated = pd.concat([submission_random_forest, i], ignore_index="true", axis=1)
submission_renamed_columns = submission_concatenated.rename(columns={0: "building_id", 1: "damage_grade"})
filepath = Path('./submission_random_forest_1.csv')  
filepath.parent.mkdir(parents=True, exist_ok=True)  
submission_renamed_columns.to_csv(filepath, index=False)
